In [52]:
import requests

# ESRI World Imagery service URL
service_url = "https://services.arcgisonline.com/arcgis/rest/services/World_Imagery/MapServer"
# Coordinates of interest (longitude, latitude)
longitude = 86.31222962  # example for San Francisco, CA
latitude = 25.48485807
radius = 500*(1/111/1000)
# Define zoom level by setting the map extent (smaller extents mean higher zoom)
map_extent = f'{longitude - radius},{latitude - radius},{longitude + radius},{latitude + radius}'  # A small extent implies a high zoom level
# Set image display parameters (affects the scale/zoom level)
image_display = '800,600,96'  # width, height, DPI
# Construct the request URL for the Identify operation
identify_url = f"{service_url}/identify"
params = {
    'f': 'json',  # format response as JSON
    'geometry': f'{longitude},{latitude}',
    'geometryType': 'esriGeometryPoint',
    'sr': '4326',  # spatial reference (WGS 84)
    'layers': 'all',
    'tolerance': 1,
    'mapExtent': map_extent,  # Define zoom level through map extent
    'imageDisplay': image_display,  # Resolution affects zoom level
    'returnGeometry': 'false',
    'returnCatalogItems': 'true'
}
# Send the request
response = requests.get(identify_url, params=params)
data = response.json()
# Extract relevant information
if 'results' in data:
    for result in data['results']:
        if 'attributes' in result and 'SRC_DATE' in result['attributes']:
            capture_date = result['attributes']['SRC_DATE']
            print(f"Capture Date: {capture_date}")
else:
    print("No data available for the specified location.")


Capture Date: Null
Capture Date: 20220308
Capture Date: 20220308
Capture Date: 20220308
Capture Date: 20220308
Capture Date: 20220308
Capture Date: 20220308
Capture Date: 20220308
Capture Date: Null
Capture Date: Null


In [53]:
map_extent

'86.30772511549549,25.4803535654955,86.3167341245045,25.489362574504504'

In [26]:
# data

In [48]:
import requests
from PIL import Image
from io import BytesIO

# ESRI World Imagery service URL
service_url = "https://services.arcgisonline.com/arcgis/rest/services/World_Imagery/MapServer"

# Object ID obtained from the Identify operation
object_id = 2755404  # Replace with your actual Object ID

# Coordinates of interest (longitude, latitude)
# longitude = -122.4194  # example for San Francisco, CA
# latitude = 37.7749

# Construct the request URL for the Export operation
export_url = f"{service_url}/export"

params = {
    'f': 'json',  # or 'image' if you want to directly retrieve the image
    'bbox': map_extent,  # bounding box around the point
    'bboxSR': '4326',  # spatial reference of bbox (WGS 84)
    'size': '800,600',  # image size in pixels
    'imageSR': '4326',  # spatial reference of the image (WGS 84)
    'layers': f'show:{object_id}',  # Show only the layer containing the object ID
    'transparent': 'true',
    'format': 'png',  # format of the output image
    'dpi': '96',
}

# Send the request
response = requests.get(export_url, params=params)

# # Check if the request was successful
# if response.status_code == 200:
#     # Open the image from the response content
#     image = Image.open(BytesIO(response.content))
#     image.show()  # This will display the image
# else:
#     print(f"Failed to fetch image. Status code: {response.status_code}")


In [49]:
response.content

b'{"href":"https://services.arcgisonline.com/arcgis/rest/directories/arcgisoutput/World_Imagery_MapServer/_ags_map23f2229a1777435591cbdc34721c1743.png","width":800,"height":600,"extent":{"xmin":86.306223613993993,"ymin":25.480353565495491,"xmax":86.318235626006,"ymax":25.489362574504497,"spatialReference":{"wkid":4326,"latestWkid":4326}},"scale":6310.2589108285883}'

In [50]:
import requests
import numpy as np
import xarray as xr
from PIL import Image
from io import BytesIO
import json

def fetch_image_as_dataarray(response_content):
    # Parse the JSON content from the response
    response_data = json.loads(response_content)
    
    # Extract the necessary information
    image_url = response_data['href']
    xmin = response_data['extent']['xmin']
    ymin = response_data['extent']['ymin']
    xmax = response_data['extent']['xmax']
    ymax = response_data['extent']['ymax']
    width = response_data['width']
    height = response_data['height']
    
    # Step 1: Download the image from the URL
    image_response = requests.get(image_url)
    image = Image.open(BytesIO(image_response.content))
    
    # Ensure the image is in RGB mode
    if image.mode != 'RGB':
        image = image.convert('RGB')
    
    # Step 2: Convert the image to a NumPy array
    image_array = np.array(image)
    
    # Step 3: Create the xarray DataArray using the spatial extent
    # Define the coordinates for the DataArray
    x_coords = np.linspace(xmin, xmax, width)
    y_coords = np.linspace(ymin, ymax, height)
    
    # Handle the three channels (R, G, B)
    data_array = xr.DataArray(image_array, coords=[y_coords, x_coords, ['R', 'G', 'B']], dims=["y", "x", "band"])
    
    return data_array

# Example usage:
# Suppose


In [51]:
ds = fetch_image_as_dataarray(response.content)
ds

<xarray.DataArray (y: 600, x: 800, band: 3)> Size: 1MB
array([[[ 84,  99,  67],
        [ 83,  92,  66],
        [ 83,  91,  60],
        ...,
        [ 68,  84,  58],
        [ 59,  77,  51],
        [ 59,  77,  51]],

       [[ 76,  91,  60],
        [ 75,  84,  59],
        [ 68,  84,  58],
        ...,
        [ 59,  77,  51],
        [ 59,  77,  51],
        [ 59,  77,  51]],

       [[ 68,  84,  58],
        [ 67,  82,  53],
        [ 75,  84,  59],
        ...,
...
        ...,
        [107,  93,  74],
        [123, 102,  82],
        [147, 126, 106]],

       [[ 60,  84,  57],
        [ 52,  76,  51],
        [ 52,  76,  51],
        ...,
        [ 91,  85,  66],
        [132, 117,  98],
        [146, 118,  98]],

       [[ 60,  84,  57],
        [ 52,  76,  51],
        [ 52,  76,  51],
        ...,
        [ 83,  77,  58],
        [107, 100,  75],
        [115, 101,  82]]], dtype=uint8)
Coordinates:
  * y        (y) float64 5kB 25.48 25.48 25.48 25.48 ... 25.49 25.49 25.49 25.49
  * x        (x) float64 6kB 86.31 86.31 86.31 86.31 ... 86.32 86.32 86.32 86.32
  * band     (band) <U1 12B 'R' 'G' 'B'

In [39]:
import hvplot.xarray

In [63]:
import requests
import numpy as np
import xarray as xr
from PIL import Image
from io import BytesIO
import json

def fetch_and_reproject_dataset(bbox, resolution):
    xmin, ymin, xmax, ymax = bbox
    service_url = "https://services.arcgisonline.com/arcgis/rest/services/World_Imagery/MapServer/identify"
    
    # Query for available data within the bounding box
    params = {
        'f': 'json',
        'geometry': f'{(xmin + xmax) / 2},{(ymin + ymax) / 2}',
        'geometryType': 'esriGeometryPoint',
        'sr': '4326',
        'mapExtent': f'{xmin},{ymin},{xmax},{ymax}',
        'imageDisplay': f'{int((xmax-xmin)/resolution)},{int((ymax-ymin)/resolution)},96',
        'tolerance': 1,
        'returnGeometry': 'false',
        'returnCatalogItems': 'true',
    }
    print(params)
    response = requests.get(service_url, params=params)
    response_data = response.json()
    #return response_data
    # Create a dictionary to store DataArrays with capture date as key
    data_arrays = {}
    
    for result in response_data.get('results', []):
        if 'attributes' in result and 'DATE (YYYYMMDD)' in result['attributes']:
            capture_date = result['attributes']['DATE (YYYYMMDD)']
            
            # Fetch image using the export operation
            image_url = f"https://services.arcgisonline.com/arcgis/rest/services/World_Imagery/MapServer/export"
            export_params = {
                'bbox': f'{xmin},{ymin},{xmax},{ymax}',
                'bboxSR': '4326',
                'size': f'{int((xmax-xmin)/resolution)},{int((ymax-ymin)/resolution)}',
                'imageSR': '4326',
                'format': 'png',
                'transparent': 'true',
                'f': 'image'
            }
            image_response = requests.get(image_url, params=export_params)
            image = Image.open(BytesIO(image_response.content))
            
            if image.mode != 'RGB':
                image = image.convert('RGB')
            
            # Convert to a NumPy array and create xarray DataArray
            image_array = np.array(image)
            x_coords = np.linspace(xmin, xmax, image_array.shape[1])
            y_coords = np.linspace(ymin, ymax, image_array.shape[0])
            data_array = xr.DataArray(image_array, coords=[y_coords, x_coords, ['R', 'G', 'B']], dims=["y", "x", "band"])
            
            # Store the DataArray in the dictionary with capture date as the key
            data_arrays[capture_date] = data_array
    
    # Combine all DataArrays into a Dataset
    dataset = xr.Dataset(data_arrays)
    
    return dataset

# Example usage:
bbox = (-122.426, 37.7699, -122.412, 37.7799)  # Example bounding box
resolution = 0.00001  # Example resolution in degrees

dataset = fetch_and_reproject_dataset(bbox, resolution)
print(dataset)


{'f': 'json', 'geometry': '-122.41900000000001,37.7749', 'geometryType': 'esriGeometryPoint', 'sr': '4326', 'mapExtent': '-122.426,37.7699,-122.412,37.7799', 'imageDisplay': '1399,999,96', 'tolerance': 1, 'returnGeometry': 'false', 'returnCatalogItems': 'true'}
<xarray.Dataset> Size: 4MB
Dimensions:   (y: 999, x: 1399, band: 3)
Coordinates:
  * y         (y) float64 8kB 37.77 37.77 37.77 37.77 ... 37.78 37.78 37.78
  * x         (x) float64 11kB -122.4 -122.4 -122.4 ... -122.4 -122.4 -122.4
  * band      (band) <U1 12B 'R' 'G' 'B'
Data variables:
    20220616  (y, x, band) uint8 4MB 138 140 124 138 140 ... 101 77 95 116 82


In [67]:
import requests
import numpy as np
import xarray as xr
from PIL import Image
from io import BytesIO
import json
import pyproj
from shapely.geometry import box
import geopandas as gpd

def wgs84_to_utm(lon, lat):
    # Determine UTM zone
    utm_zone = int((lon + 180) / 6) + 1
    utm_crs = pyproj.CRS(f"EPSG:326{utm_zone}" if lat >= 0 else f"EPSG:327{utm_zone}")
    
    # Define transformer to convert from WGS84 to UTM
    transformer = pyproj.Transformer.from_crs("EPSG:4326", utm_crs, always_xy=True)
    
    # Perform the transformation
    easting, northing = transformer.transform(lon, lat)
    
    return easting, northing, utm_crs.to_epsg()

def fetch_and_reproject_dataset_utm(bbox, resolution):
    xmin, ymin, xmax, ymax = bbox
    
    # Convert bounding box to UTM
    xmin_utm, ymin_utm, utm_epsg = wgs84_to_utm(xmin, ymin)
    xmax_utm, ymax_utm, _ = wgs84_to_utm(xmax, ymax)
    
    service_url = "https://services.arcgisonline.com/arcgis/rest/services/World_Imagery/MapServer/identify"
    
    # Query for available data within the UTM bounding box
    params = {
        'f': 'json',
        'geometry': f'{(xmin_utm + xmax_utm) / 2},{(ymin_utm + ymax_utm) / 2}',
        'geometryType': 'esriGeometryPoint',
        'sr': utm_epsg,  # Use the UTM spatial reference
        'mapExtent': f'{xmin_utm},{ymin_utm},{xmax_utm},{ymax_utm}',
        'imageDisplay': f'{int((xmax_utm-xmin_utm)/resolution)},{int((ymax_utm-ymin_utm)/resolution)},96',
        'tolerance': 1,
        'returnGeometry': 'false',
        'returnCatalogItems': 'true',
    }
    
    response = requests.get(service_url, params=params)
    response_data = response.json()
    
    # Create a dictionary to store DataArrays with capture date as key
    data_arrays = {}
    
    for result in response_data.get('results', []):
        if 'attributes' in result and 'DATE (YYYYMMDD)' in result['attributes']:
            capture_date = result['attributes']['DATE (YYYYMMDD)']
            
            # Fetch image using the export operation
            image_url = f"https://services.arcgisonline.com/arcgis/rest/services/World_Imagery/MapServer/export"
            export_params = {
                'bbox': f'{xmin_utm},{ymin_utm},{xmax_utm},{ymax_utm}',
                'bboxSR': utm_epsg,
                'size': f'{int((xmax_utm-xmin_utm)/resolution)},{int((ymax_utm-ymin_utm)/resolution)}',
                'imageSR': utm_epsg,
                'format': 'png',
                'transparent': 'true',
                'f': 'image'
            }
            image_response = requests.get(image_url, params=export_params)
            image = Image.open(BytesIO(image_response.content))
            
            if image.mode != 'RGB':
                image = image.convert('RGB')
            
            # Convert to a NumPy array and create xarray DataArray
            image_array = np.array(image)
            x_coords = np.linspace(xmin_utm, xmax_utm, image_array.shape[1])
            y_coords = np.linspace(ymin_utm, ymax_utm, image_array.shape[0])
            data_array = xr.DataArray(image_array, coords=[y_coords, x_coords, ['R', 'G', 'B']], dims=["y", "x", "band"])
            
            # Store the DataArray in the dictionary with capture date as the key
            data_arrays[capture_date] = data_array
    
    # Combine all DataArrays into a Dataset
    dataset = xr.Dataset(data_arrays)
    
    return dataset

# Example usage:
bbox = (-122.426, 37.7699, -122.412, 37.7799)  # Example bounding box in WGS 84
resolution = 1 # Example resolution in meters for UTM

dataset = fetch_and_reproject_dataset_utm(bbox, resolution)
print(dataset)


<xarray.Dataset> Size: 4MB
Dimensions:   (y: 1117, x: 1226, band: 3)
Coordinates:
  * y         (y) float64 9kB 4.18e+06 4.18e+06 4.18e+06 ... 4.182e+06 4.182e+06
  * x         (x) float64 10kB 5.506e+05 5.506e+05 ... 5.518e+05 5.518e+05
  * band      (band) <U1 12B 'R' 'G' 'B'
Data variables:
    20220616  (y, x, band) uint8 4MB 127 105 88 131 102 74 ... 108 92 97 72 49


In [ ]:
# dataset.y.values[1]-dataset.y.values[0]

In [65]:
dataset.hvplot.rgb(bands='band',width=1400,height=999,x='x',y='y')

:RGB   [x,y]   (R,G,B)

In [11]:
image_array.shape

(600, 800)